In [ ]:
import numpy as np
import pandas as pd
import seaborn as sns
import geopandas
import matplotlib.pyplot as plt

#raw data
df=pd.read_csv(r'data/CSPDS.csv')

#df['County'] = df['Region Name'].str.split(' ')[0]

#code for calculating chloropleth
zip = geopandas.read_file('shapefiles/cb_2018_us_zcta510_500k.shp')
counties =geopandas.read_file('shapefiles/cb_2018_us_county_20m.shp')
#csa = geopandas.read_file('shapefiles/cb_2018_us_csa_20m.shp')
states = geopandas.read_file('shapefiles/cb_2018_us_state_20m.shp')
#print(csa.head())

zip = zip.to_crs("EPSG:3395")
counties=counties.to_crs("EPSG:3395")
#csa = csa.to_crs("EPSG:3395")
states = states.to_crs("EPSG:3395")
        

#Alaska and Hawaii excluded due to lack of CSA
states=states[states['NAME'] != 'Alaska']
states=states[states['NAME'] != 'Hawaii']
states=states[states['NAME'] != 'Puerto Rico']

counties=counties[counties['STATEFP'] != '02']
counties=counties[counties['STATEFP'] != '15']
counties=counties[counties['STATEFP'] != '72']

us_boundary_map = states.boundary.plot(figsize=(18, 12),color="Black", linewidth=.1)
#.plot(figsize=(18, 12),color="Black", linewidth=.1)
counties.plot(ax=us_boundary_map, cmap='magma')
counties
#zip

In [ ]:
import folium





In [ ]:




from fredapi import Fred
fred = Fred(api_key='d7f545fe7858da4279909dd26a7b28cc')
data = fred.get_series('DAAA')
data.plot()
data
print

In [ ]:


print(type(data))
data


In [ ]:

from datetime import datetime

#convert time

year= '2020'

year_dt = datetime.strptime(year, '%Y')

print(str(year_dt.date()))


In [ ]:
import folium
import io
import pandas as pd

import os
cwd = os.getcwd()
os.chdir(cwd)


county_map=r'shapefiles/cb_2018_us_county_20m.geojson'

        

#coordinate = (37.8199286, -122.4782551)
m = folium.Map(
    tiles='CartoDB positron',
    location=[48, -102],
    zoom_start=3,            
)

folium.GeoJson(county_map, name="geojson").add_to(m)

#folium.GeoJson(open(county_map).read()).add_to(m)

# folium.TopoJson(
#    open(county_map)).add_to(m)

#folium.Choropleth(open(county_map)).add_to(m)

#folium.Choropleth(geo_data=county_map).add_to(m)

#  folium.Choropleth(
    #  geo_data=county_map,
    # name="choropleth",
    # data=state_data,
    # columns=["State", "Unemployment"],
    # key_on="feature.id",
    #fill_color="YlGn",
    #fill_opacity=0.7,
    # line_opacity=0.2,
    #legend_name="Median Housing Price Correlations",
# ).add_to(m)



folium.LayerControl().add_to(m)



m

In [7]:
import branca
import json
import requests

county_data = r'shapefiles/us_county_data.csv'
county_geo = r'shapefiles/us_counties_20m_topo.json'


df = pd.read_csv(county_data, na_values=[" "])

colorscale = branca.colormap.linear.YlOrRd_09.scale(0, 50e3)
employed_series = df.set_index("FIPS_Code")["Employed_2011"]


def style_function(feature):
    employed = employed_series.get(int(feature["id"][-5:]), None)
    return {
        "fillOpacity": 0.5,
        "weight": 0,
        "fillColor": "#black" if employed is None else colorscale(employed),
    }


m = folium.Map(location=[48, -102], tiles="cartodbpositron", zoom_start=3)

folium.TopoJson(
    open(county_geo),
    "objects.us_counties_20m",
    style_function=style_function,
).add_to(m)


m




In [6]:
import folium
import io
import pandas as pd
import json
import requests
import os

county_data = r'shapefiles/us_county_data.csv'
#county_geo = r'shapefiles/gz_2010_us_050_00_20m.json'
county_geo = r'shapefiles/cb_2018_us_county_20m.geojson'


df = pd.read_csv(county_data, na_values=[" "])
print(df.dtypes)
df["FIPS_Code"] = df["FIPS_Code"].astype(str)
print(df.dtypes)

m = folium.Map(location=[48, -102], tiles="cartodbpositron", zoom_start=3)

#folium.GeoJson(county_geo, name="geojson").add_to(m)

bins = list(df["Unemployment_rate_2011"].quantile([0, 0.25, 0.5, 0.75, 1]))


folium.Choropleth(
    geo_data= county_geo,
    name="choropleth",
    data=df,
    columns=["FIPS_Code","Unemployment_rate_2011"],
    key_on="properties.GEOID",
    fill_color="YlGnBu",
    fill_opacity=0.7,
    line_opacity=0.5,
    legend_name="Unemployment Rate (%)",
    bins=bins,
    reset=True,
).add_to(m)

folium.LayerControl().add_to(m)

m





FIPS_Code                                     int64
State                                        object
Area_name                                    object
Civilian_labor_force_2011                   float64
Employed_2011                               float64
Unemployed_2011                             float64
Unemployment_rate_2011                      float64
Median_Household_Income_2011                float64
Med_HH_Income_Percent_of_StateTotal_2011    float64
dtype: object
FIPS_Code                                    object
State                                        object
Area_name                                    object
Civilian_labor_force_2011                   float64
Employed_2011                               float64
Unemployed_2011                             float64
Unemployment_rate_2011                      float64
Median_Household_Income_2011                float64
Med_HH_Income_Percent_of_StateTotal_2011    float64
dtype: object


In [5]:



import pandas as pd

url = (
    "https://raw.githubusercontent.com/python-visualization/folium/master/examples/data"
)
state_geo = f"{url}/us-states.json"
state_unemployment = f"{url}/US_Unemployment_Oct2012.csv"
state_data = pd.read_csv(state_unemployment)

m = folium.Map(location=[48, -102], zoom_start=3)

folium.Choropleth(
    geo_data=state_geo,
    name="choropleth",
    data=state_data,
    columns=["State", "Unemployment"],
    key_on="feature.id",
    fill_color="YlGn",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Unemployment Rate (%)",
).add_to(m)

folium.LayerControl().add_to(m)

m



NameError: name 'folium' is not defined

## Import FRED data

In [9]:
import pandas as pd
from fredapi import Fred
from pandas_datareader import data

fred = Fred(api_key='d7f545fe7858da4279909dd26a7b28cc')

df = {}

df['CASE-SHILLER'] = fred.get_series('CSUSHPISA', observation_start='1/31/1996') #S&P/Case-Shiller U.S. National Home Price Index
df['CPI'] = fred.get_series('CPIAUCSL', observation_start='1/31/1996') #Consumer Price Index for All Urban Consumers: All Items in U.S. City Average
df['M2'] = fred.get_series('WM2NS', observation_start='1/31/1996')#M2 Money Stock
df['EFFR'] = fred.get_series('EFFR', observation_start='1/31/1996')#Effective Federal Funds Rate
df['10YR'] = fred.get_series('DGS10', observation_start='1/31/1996') #10-Year Treasury Constant Maturity Rate
df['30YR_MORT'] = fred.get_series('MORTGAGE30US', observation_start='1/31/1996') #30-Year Fixed Rate Mortgage Average in the United States
df['PERS_SAV'] = fred.get_series('PSAVERT', observation_start='1/31/1996') #Personal Saving Rate
df['WTI_OIL'] = fred.get_series('DCOILWTICO', observation_start='1/31/1996') #Crude Oil Prices: West Texas Intermediate (WTI) - Cushing, Oklahoma
df['BUSLOANS'] = fred.get_series('BUSLOANS', observation_start='1/31/1996')#Commercial and Industrial Loans, All Commercial Banks
df['CORP_BOND'] = fred.get_series('DAAA', observation_start='1/31/1996')#Moody's Seasoned Aaa Corporate Bond Yield
df = pd.DataFrame(df).resample('M').mean()
#df=df.dropna()

#import SPY data 
start_date = pd.to_datetime('1996-01-31')
end_date = pd.to_datetime('2021-04-30')

# User pandas_reader.data.DataReader to load the desired data. As simple as that.
panel_data = data.DataReader('SPY','yahoo', start_date, end_date)
spy=panel_data['Adj Close'].to_frame().resample('M').mean()

#add_df = pd.concat([df, spy])
add_df = df.merge(spy, left_index=True, right_index=True)

del df, panel_data, spy
add_df


CASE-SHILLER      CPI         M2      EFFR      10YR  30YR_MORT  \
1996-01-31        81.839  154.700        NaN       NaN  5.600000        NaN   
1996-02-29        81.957  155.000   3644.800       NaN  5.805500     7.0750   
1996-03-31        82.198  155.500   3689.150       NaN  6.268571     7.6240   
1996-04-30        82.425  156.100   3717.560       NaN  6.511364     7.9250   
1996-05-31        82.613  156.400   3689.325       NaN  6.736818     8.0700   
...                  ...      ...        ...       ...       ...        ...   
2020-12-31       235.442  261.560  19263.075  0.090000  0.933636     2.6840   
2021-01-31       238.421  262.231  19392.500  0.085263  1.081053     2.7350   
2021-02-28       241.130  263.161  19500.950  0.075789  1.257895     2.8100   
2021-03-31           NaN  264.793  19907.440  0.069565  1.610870     3.0825   
2021-04-30           NaN      NaN  20360.600  0.069524  1.634286     3.0600   

            PERS_SAV    WTI_OIL   BUSLOANS  CORP_BOND   Adj Close  
1996-01-31       6.7  17.760000   721.8113   6.780000   40.386723  
1996-02-29       6.7  19.093500   724.1688   6.986500   41.266317  
1996-03-31       6.6  21.332381   727.3440   7.346190   41.229702  
1996-04-30       5.7  23.497143   732.0751   7.502273   41.228810  
1996-05-31       6.7  21.165455   736.4421   7.623636   42.264314  
...              ...        ...        ...        ...         ...  
2020-12-31      13.5  47.025000  2617.1983   2.260909  366.761912  
2021-01-31      20.0  52.008421  2582.1075   2.451053  376.943844  
2021-02-28      13.9  59.046316  2602.3242   2.700000  386.216625  
2021-03-31      27.6  62.333043  2605.4351   3.035217  389.514112  
2021-04-30       NaN  61.218235        NaN   2.896500  412.910472  

[304 rows x 11 columns]

## Data Test

In [4]:
import pandas as pd

zip_df=pd.read_csv(r'C:\Users\mattl\Documents\UVa - Data Science Masters\CS 5010\CS-5010-semester-project\data\ZIP-COUNTY-FIPS_2017-06.csv')
zip_df.rename({'STCOUNTYFP': 'GEO_ID'}, axis=1, inplace=True)
zip_df["GEO_ID"] = zip_df["GEO_ID"].astype(str)
#print(zip_df.head())


df1=pd.read_csv(r'C:\Users\mattl\Documents\UVa - Data Science Masters\CS 5010\CS-5010-semester-project\data\Zip_zhvi_bdrmcnt_1_uc_sfrcondo_tier_0.33_0.67_sm_sa_mon.csv')
df1['Bedrooms'] = '1'
df1_melt = pd.melt(df1, id_vars=['RegionID', 'SizeRank', 'RegionName', 'RegionType', 'StateName','State', 'City', 'Metro', 'CountyName', 'Bedrooms'], var_name='Date', value_name='price_index')

df2=pd.read_csv(r'C:\Users\mattl\Documents\UVa - Data Science Masters\CS 5010\CS-5010-semester-project\data\Zip_zhvi_bdrmcnt_2_uc_sfrcondo_tier_0.33_0.67_sm_sa_mon.csv')
df2['Bedrooms'] = '2'
df2_melt = pd.melt(df2, id_vars=['RegionID', 'SizeRank', 'RegionName', 'RegionType', 'StateName','State', 'City', 'Metro', 'CountyName', 'Bedrooms'], var_name='Date', value_name='price_index')

df3=pd.read_csv(r'C:\Users\mattl\Documents\UVa - Data Science Masters\CS 5010\CS-5010-semester-project\data\Zip_zhvi_bdrmcnt_3_uc_sfrcondo_tier_0.33_0.67_sm_sa_mon.csv')
df3['Bedrooms'] = '3'
df3_melt = pd.melt(df3, id_vars=['RegionID', 'SizeRank', 'RegionName', 'RegionType', 'StateName','State', 'City', 'Metro', 'CountyName', 'Bedrooms'], var_name='Date', value_name='price_index')

df4=pd.read_csv(r'C:\Users\mattl\Documents\UVa - Data Science Masters\CS 5010\CS-5010-semester-project\data\Zip_zhvi_bdrmcnt_4_uc_sfrcondo_tier_0.33_0.67_sm_sa_mon.csv')
df4['Bedrooms'] = '4'
df4_melt = pd.melt(df4, id_vars=['RegionID', 'SizeRank', 'RegionName', 'RegionType', 'StateName','State', 'City', 'Metro', 'CountyName', 'Bedrooms'], var_name='Date', value_name='price_index')

df5=pd.read_csv(r'C:\Users\mattl\Documents\UVa - Data Science Masters\CS 5010\CS-5010-semester-project\data\Zip_zhvi_bdrmcnt_5_uc_sfrcondo_tier_0.33_0.67_sm_sa_mon.csv')
df5['Bedrooms'] = '5'
df5_melt = pd.melt(df5, id_vars=['RegionID', 'SizeRank', 'RegionName', 'RegionType', 'StateName','State', 'City', 'Metro', 'CountyName', 'Bedrooms'], var_name='Date', value_name='price_index')


df = pd.concat([df1_melt, df2_melt, df3_melt, df4_melt, df5_melt], axis=0)
df.rename({'RegionName': 'ZIP'}, axis=1, inplace=True)
del df1,df2,df3,df4,df5,df1_melt,df2_melt,df3_melt,df4_melt,df5_melt

df_merge=df.merge(zip_df, how='left')
df_merge['Date']=pd.to_datetime(df_merge['Date'])
df_merge=df_merge.set_index('Date') #foundational to time series
del df

final_df = df_merge.merge(add_df, left_index=True, right_index=True)
final_df

RegionID  SizeRank    ZIP RegionType StateName State         City  \
1996-01-31     61639         0  10025        Zip        NY    NY     New York   
1996-01-31     84654         1  60657        Zip        IL    IL      Chicago   
1996-01-31     61637         2  10023        Zip        NY    NY     New York   
1996-01-31     84616         4  60614        Zip        IL    IL      Chicago   
1996-01-31     91940         5  77449        Zip        TX    TX         Katy   
...              ...       ...    ...        ...       ...   ...          ...   
2021-02-28     65438     34322  18348        Zip        PA    PA  Pocono Lake   
2021-02-28     59376     34430   4109        Zip        ME    ME     Portland   
2021-02-28     66881     34430  21405        Zip        MD    MD    Annapolis   
2021-02-28     95851     34430  89155        Zip        NV    NV    Las Vegas   
2021-02-28     66169     34430  20052        Zip        DC    DC   Washington   

                                       Metro            CountyName Bedrooms  \
1996-01-31       New York-Newark-Jersey City       New York County        1   
1996-01-31          Chicago-Naperville-Elgin           Cook County        1   
1996-01-31       New York-Newark-Jersey City       New York County        1   
1996-01-31          Chicago-Naperville-Elgin           Cook County        1   
1996-01-31  Houston-The Woodlands-Sugar Land         Harris County        1   
...                                      ...                   ...      ...   
2021-02-28                  East Stroudsburg         Monroe County        5   
2021-02-28           Portland-South Portland     Cumberland County        5   
2021-02-28         Baltimore-Columbia-Towson   Anne Arundel County        5   
2021-02-28      Las Vegas-Henderson-Paradise          Clark County        5   
2021-02-28   Washington-Arlington-Alexandria  District of Columbia        5   

            ...     WM2NS      EFFR     DGS10 UNRATE MORTGAGE30US  PSAVERT  \
1996-01-31  ...       NaN       NaN  5.600000    5.6          NaN      6.7   
1996-01-31  ...       NaN       NaN  5.600000    5.6          NaN      6.7   
1996-01-31  ...       NaN       NaN  5.600000    5.6          NaN      6.7   
1996-01-31  ...       NaN       NaN  5.600000    5.6          NaN      6.7   
1996-01-31  ...       NaN       NaN  5.600000    5.6          NaN      6.7   
...         ...       ...       ...       ...    ...          ...      ...   
2021-02-28  ...  19500.95  0.075789  1.257895    6.2         2.81     13.9   
2021-02-28  ...  19500.95  0.075789  1.257895    6.2         2.81     13.9   
2021-02-28  ...  19500.95  0.075789  1.257895    6.2         2.81     13.9   
2021-02-28  ...  19500.95  0.075789  1.257895    6.2         2.81     13.9   
2021-02-28  ...  19500.95  0.075789  1.257895    6.2         2.81     13.9   

            DCOILWTICO   BUSLOANS  DAAA   Adj Close  
1996-01-31   17.760000   721.8113  6.78   40.386723  
1996-01-31   17.760000   721.8113  6.78   40.386723  
1996-01-31   17.760000   721.8113  6.78   40.386723  
1996-01-31   17.760000   721.8113  6.78   40.386723  
1996-01-31   17.760000   721.8113  6.78   40.386723  
...                ...        ...   ...         ...  
2021-02-28   59.046316  2602.3242  2.70  386.216625  
2021-02-28   59.046316  2602.3242  2.70  386.216625  
2021-02-28   59.046316  2602.3242  2.70  386.216625  
2021-02-28   59.046316  2602.3242  2.70  386.216625  
2021-02-28   59.046316  2602.3242  2.70  386.216625  

[53692278 rows x 28 columns]

## Import FRED data

## Join Main df with financial data

In [ ]:
final_df = df_merge.merge(add_df, left_index=True, right_index=True)
final_df

In [11]:
import pandas as pd


state_data = r'shapefiles/us_county_data.csv'
        
df = pd.read_csv(state_data, na_values=[" "])

df_min=pd.DataFrame()
df_min=df.groupby('State', as_index=False)['Unemployment_rate_2011'].mean()
print(df_min.info())
df_min


<class 'pandas.core.frame.DataFrame'>
Int64Index: 53 entries, 0 to 52
Data columns (total 2 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   State                   53 non-null     object 
 1   Unemployment_rate_2011  53 non-null     float64
dtypes: float64(1), object(1)
memory usage: 1.2+ KB
None


State  Unemployment_rate_2011
0     AK               10.080000
1     AL               10.461765
2     AR                8.952632
3     AZ               12.162500
4     CA               13.393220
5     CO                7.675385
6     CT                8.588889
7     DC               10.200000
8     DE                7.325000
9     FL               10.238235
10    GA               10.773750
11    HI                7.800000
12    IA                5.905000
13    ID                9.135556
14    IL                9.368932
15    IN                9.111828
16    KS                5.533019
17    KY               10.276033
18    LA                8.503077
19    MA                7.453333
20    MD                7.768000
21    ME                8.282353
22    MI               11.007143
23    MN                6.642045
24    MO                8.729310
25    MS               12.161446
26    MT                6.556140
27    NC               11.237624
28    ND                3.835185
29    NE                4.018085
30    NH                5.463636
31    NJ                9.600000
32    NM                7.538235
33    NV               11.511111
34    NY                8.226984
35    OH                9.458427
36    OK                6.042308
37    OR               10.354054
38    PA                8.050000
39    PR               17.750633
40    RI               10.600000
41    SC               12.014894
42    SD                5.102985
43    TN               10.592708
44    TX                7.386667
45    US                9.000000
46    UT                7.396667
47    VA                7.536296
48    VT                6.086667
49    WA                9.955000
50    WI                8.039726
51    WV                8.885714
52    WY                5.900000